# Trabajo práctico Nº 3: Cúmulos abiertos

Notebook creada por Tomás Ansin (2021) y modificada por G. Ferrero (2022, 2023)


## Guía para realizar la práctica con python

#### Como ya usamos varios comandos de python en las prácticas anteriores, en esta les proponemos una serie de ejemplos que no están exactamente en el mismo orden que la práctica por una cuestión didáctica. Pero son todos los necesarios para poder resolverla. De cualquier manera si hay algo que no saben como hacer y no está explicado acá, no duden en consultar.

#### Vamos a utilizar pandas para manejar tablas, como en las prácticas anteriores.
Si están trabajando en una computadora local o en otra plataforma que no sea Astro Data Lab, y no tienen instalado pandas, pueden instalarlo con conda o pip segun como hayan instalado python y Jupyter en su máquina, con estos comandos:

pip install pandas (si usan colab ejecuten este comando en la primera celda)

o: conda install pandas

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.patches import Rectangle
import pandas as pd     # usaremos pandas para esta práctica
plt.style.use('../sisest.mplstyle')

### 1. Descargue de Vizier los datos fotométricos y espectroscópicos del cúmulo abierto NGC 2516 
### (Sung et al. 2002, http://adsabs.harvard.edu/abs/2002AJ....123..290S)
### y guárdelos en un archivo con nombre NGC2516_fot.dat 
### Luego importe ese archivo en el mismo directorio en el que está esta Notebook.
### Utilizando esos datos, haga lo siguiente:

#### a) Grafique los diagramas $(B-V,V)$, $(U-B,V)$ y $(B-V,U-B)$. Señale los límites aproximados que contienen a las estrellas de la secuencia principal del cúmulo en los diagramas color-magnitud.


In [ ]:
# Veamos cómo es la tabla

!head NGC2516_fot.dat -n 15

### Para leer la tabla podemos usar read_csv() de pandas

Argumentos: **sep** indica cómo están separadas las columnas, 
**skiprows** salta las primeras 6 líneas

In [ ]:
sung = pd.read_csv('NGC2516_fot.dat', sep = ';', skiprows = 6)

# ahora miramos las primeras línea del dataframe

sung.head()


### Notemos que hay una primera columna que no tiene nombre, esa columna se llama *index* y más adelante la utilizaremos.

### Para ver una pequeña descripción estadistica de los valores que tenemos en las columnas usamos *describe*

In [ ]:
sung.describe()


#### Recordemos que podemos acceder a las columnas de dos maneras. La primera es usando ['nombre_columna']

In [ ]:
sung['Vmag']

#### Y la segunda es con dataframe.nombre_columna

In [ ]:
sung.Vmag

#### Para usar la segunda los nombres de las columnas no deben contener caracteres especiales (no usar "-" por ejemplo).
#### Se pueden utilizar los dos de manera indiferente, como vemos en este ejemplo con plot


In [ ]:
plt.plot(sung['BV'], sung.Vmag, '.') 

#### A continuación creemos un gráfico como nos piden los lineamientos. Como queremos que aparezcan las barras de errores usaremos *errorbar*
#### El formato del comando es:
#### plt.errorbar(*columna_eje_x*, *columna_eje_y*, xerr = *columna_error_x*, yerr = *columna_error_y*, fmt = '*formato_punto*')
#### y para que el eje en magnitudes aparezca invertido podemos usar
#### *plt.gca().invert_yaxis()*
#### No olvidemos colocar etiquetas en los ejes, unidades, etc.

#### También podemos graficar usando directamente pandas con la funcion plot()
#### La sintaxis del formato es:
#### tabla.plot(kind = 'line', x = 'BV', y = 'Vmag', xerr = 'e_BV', yerr = 'e_V', fmt='.', capsize = 2, legend = False)
#### Para darle estilo (nombre de los ejes, titulo, grilla, etc.) podemos usar *pyplot* (o sea *plt.*) como antes.

## Filtrar tablas

#### Repasemos como filtrar tablas en pandas. 
#### Supongamos que queremos aquellos cúmulos que tienen V < 10 y e_V < 0.01

In [ ]:
# Si hacemos esto

sung.Vmag < 10

#### La celda anterior devuelve una lista de variables booleanas. Si le pasamos eso como argumento al dataframe *sung*, obtenemos una tabla que contiene sólo las filas con valor *True*.

In [ ]:
# Entre corchetes va la condición

sung[sung.Vmag<10]

# ¡notemos que faltan algunas filas (la 0 y la 6 por ejemplo)... y muchas más!
# eso es justamente porque filtramos varias filas

#### Los filtros pueden contener operaciones lógicas como "y" ("and") que se escribe: *&* (esto es útil para ejercicio 1b).
#### Por ejemplo:

In [ ]:
sung[(sung.Vmag < 10) & (sung.e_V < 0.01)]

## ¡Ojo que esto no cambia el dataframe! Solamente está mostrando las líneas que cumplen con la condición pedida. 

## Para guardar la salida hay que sobreescribir el dataframe o guardarlo en una nueva variable.

### Otra cosa interesantes es que se pueden hacer operaciones sobre las columnas fácilmente. Por ejemplo para sumar todos los valores de una columna (útil para ejercicio 1b) se puede hacer:

In [ ]:
# Sumemos las magnitudes V por ejemplo

sung.Vmag.sum()

#### Sabiendo esto podemos generar una nueva tabla que contenga solamente con las estrellas de las cuales conocemos el  tipo espectral.
#### Por ejemplo así:

In [ ]:
tabla_esp = sung[~sung.SpType.isna()]

# isna() devuelve sólo las líneas que contienen NaN en SpType, con el ~ adelante, hace lo contrario.
# si las líneas con tipo espectral desconocido tienen otro caracter en esa columna, que no sea un NaN, hay que modificar 
# adecuadamente la condición.

# veamos qué quedó en la tabla para chequear

tabla_esp

#### Si queremos quedarnos solamente con las estrellas enanas (clase de luminosidad V)
#### Podemos usar *str.contains('V')* lo que significa que el string tiene que contener el caracter 'V' para que devuelva True.
#### Si además queremos eliminar las subgigantes, podemos hacer así:

In [ ]:
# Contener 'V' y no 'I' para que no agregue las sub-gigantes

tabla_sp = tabla_esp[tabla_esp.SpType.str.contains('V') & ~tabla_esp.SpType.str.contains('I')]

tabla_sp

#### Hay algunas estrellas que tienen tipos espectrales raros. Esas las podemos sacar una por una con la función *drop()*
#### (Ver el ejemplo para eliminar la fila 18 y repetir para las filas que sea necesario)

In [ ]:
tabla_sp = tabla_sp.drop(18) # Usamos el index para indicar la fila que eliminamos

tabla_sp

#### Notar que los índices (columna index) siguen siendo los originales.
#### Veamos las estadísticas de la tabla_sp

In [ ]:
tabla_sp[['SpType']].describe()

### Veamos cómo importar la calibración de Schmidt-Kaler.

In [ ]:
# Tiene que estar en el directorio

!head SecPpal_SK.dat

#### Como la columna Sp tiene valores únicos vamos a usarla como índice (index) para la tabla de pandas, usando la opción index_col='Sp'

In [ ]:
# primero importamos la tabla

tabla_sk = pd.read_csv('SecPpal_SK.dat', sep=';', comment='#', index_col='Sp')

tabla_sk.head()

### Ahora los índices de las filas de esta tabla son los tipos espectrales.

#### Ahora volvemos a la tabla de datos de Sung, la que tenía solamente las estrellas con tipo espectral conocido, y nos preguntamos cuántos tipos espectrales distintos hay en ella.

In [ ]:
# el comando set genera un conjunto de elementos únicos 

print('Tabla de Sung:')

print(set(tabla_sp.SpType))

# Comparemos con la tabla de S-K

print('Tabla de Schmidt-Kaler:')

print(tabla_sk.index)

#### Notemos que en Sung hay tipos espectrales que no están en la calibración S-K. Esos los vamos a obtener interpolando. 

### Podemos acceder a cada tipo espectral de la tabla S-K así:

In [ ]:
tabla_sk.loc['A0']

### Si queremos solamente una columna de una tabla, en este caso (V, B-V o U-B) usamos [n] con n=0,1,2 para indicarla. Es importante el orden.

In [ ]:
tabla_sk.loc['A0'][0] # Valor de V para A0

### Queremos agregar a la tabla de Sung los valores de la calibración de S-K. Para eso podemos crear primero un diccionario.

#### Un diccionario es un tipo de variable en python que consiste en pares del tipo (clave: valor)

In [ ]:
# Podemos hacer un pequeño diccionario para los 8 tipos espectrales de la tabla_sp

BV_dict = dict.fromkeys(list(tabla_sp.SpType)) 
BV_dict

# notemos que el diccionario tiene las claves (los tipos espectrales) pero le faltan los valores de (B-V)

### Ahora vamos llenando ese diccionario. 

#### Empecemos por los tipos espectrales que están en la tabla S-K

In [ ]:
BV_dict['A0V'] = tabla_sk.loc['A0'][1]
BV_dict['A2V'] = tabla_sk.loc['A2'][1]
BV_dict['F0V'] = tabla_sk.loc['F0'][1]
BV_dict

#### Repitiendo esa operación podemos crear un diccionario para la magnitud V y para (U-B)

#### Luego con la función *map()* podemos agregar a los datos de Sung una columna que contenga el valor de $(B-V)_0$

#### Después, cuando terminemos de llenar el diccionario *BV_dict* con los tipos espectrales que faltan, podemos volver a correr el código de la siguiente celda.

In [ ]:
# Primero agregamos la columna 'BV0' a la tabla de Sung "mapeando" con el diccionario

tabla_sp['BV0'] = tabla_sp['SpType'].map(BV_dict) 

tabla_sp 

# Notemos que la columna de BV0 es nueva y falta completarla

### Para completarla tenemos que interpolar y obtener los valores que no están en S-K

#### Una opción sería usar la expresión $\frac{x-x_1}{x_2-x_1} = \frac{y-y_1}{y_2-y_1}$
#### donde $x_1$ y $x_2$ son números que representan los subtipos espectrales conocidos
#### $y_1$ e $y_2$ representan los valores de una variable (por ejemplo $(B-V)_0$) conocidos, para $x_1$ y $x_2$
#### $x$ representa el subtipo espectral cuyo $(B-V)_0$ no conocemos e $y$ es ese $(B-V)_0$ desconocido.
#### Entonces, será

$ y = (y_2-y_1) \frac{x-x_1}{x_2-x_1} + y_1 $

#### Por ejemplo, no conocemos $(B-V)_0$ para una A7V. Pero lo conocemos para A5 y F0.
#### Por tanto sería:

In [ ]:
x1 = 5.
x2 = 10.
y1 = 0.15 
y2 = 0.3 
# entonces para 
x = 7
y = (y2-y1)*(x-x1)/(x2-x1) + y1
y

In [ ]:
# eso mismo lo podemos hacer usando la tabla_sk, con la ventaja que lo hacemos de una vez para las
# tres variables (V, B-V y U-B)

A7 = ((tabla_sk.loc['F0'] - tabla_sk.loc['A5'])*2/5 + tabla_sk.loc['A5'])
A7

In [ ]:
# luego podemos agregar ese resultado al diccionario

BV_dict['A7V']=A7[1]

BV_dict

#### Recordemos que esto hay que repetirlo para el diccionario de V y el de (U-B). Una vez que tenemos los diccionarios completos volvemos a "mapear" la tabla de Sung con los diccionarios y tendremos asignadas las magnitudes y colores intrínsecos a cada estrella.

### Recordemos cómo agregar una columna a un arreglo o tabla a partir de otras columnas (útil para ejercicio 1.c)

In [ ]:
# Agreguemos columna nueva con valores de Vmag+5.0

sung['Col_nueva'] = sung.Vmag + 5.0
sung

#### Ahora la quitamos porque no significa nada.

In [ ]:
tabla=tabla.drop('Col_nueva', axis='columns')
tabla

#### Calcular el promedio (y la desviación estándar) de una columna con pandas es muy sencillo. Por ejemplo, calculemos el promedio de la columna *e_V*

In [ ]:
e_V_prom = sung.e_V.mean() 

e_V_std = sung.e_V.std()

print(e_V_prom, e_V_std)

#### Y también se puede calcular el promedio y la desviación estándar para los resultados de operaciones entre las columnas. Por ejemplo, para (B-V) + V

In [ ]:
Bmag = (sung.BV - sung.Vmag).mean()

std_Bmag = (sung.BV - sung.Vmag).std()

print(Bmag, std_Bmag)

#### Eso se puede usar para calcular los valores de los excesos de color del cúmulo.